In [1]:
from mpl_toolkits.basemap import Basemap  # import Basemap matplotlib toolkit
import numpy as np
import matplotlib.pyplot as plt
import pygrib # import pygrib interface to grib_api
import pandas as pd
import os
import sys
import math
import folium
import csv 
import time

start = time.time()

%matplotlib inline

root = os.getcwd()
root_data = root + "/grib_data"
root_URL = "http://database.rish.kyoto-u.ac.jp/arch/jmadata/data/gpv/original/"

#timestomp like 201808010000 means that it is at 2019/04/09/08:00(UTC timezone)
year = "2019"
month = "05"
day = "22"
roottime="000000"


def getgrib(year,month,day,roottime):
    file_name = "Z__C_RJTD_"+str(year+month+day+roottime)+"_MSM_GPV_Rjp_Lsurf_FH00-15_grib2.bin"
    file_url = root_URL\
                +str(year + "/" + month + "/" + day +"/" )\
                +file_name
    root_file= "grib_data/"+file_name
    if os.path.isfile(root_file) == False:
            command = "wget -P grib_data/ "+ file_url
            os.system(command)

    getgrib_output = pygrib.open(root_file)
    return getgrib_output

def getrootgrib(year,month,day,time):
    file_name = "Z__C_RJTD_"+str(year+month+day+roottime)+"_MSM_GPV_Rjp_Lsurf_FH00-15_grib2.bin"    
    return "grib_data/"+file_name

In [2]:
print(os.path.isfile( getrootgrib(year,month,day,roottime) ))

True


In [3]:
grbs = getgrib(year,month,day,roottime)
latlons = grbs

In [4]:
print(os.path.isfile( getrootgrib(year,month,day,roottime) ))

True


In [5]:
#check parameters in gribfile
grb_1 = grbs.select(name='Pressure reduced to MSL')[0]

# lats,lonsは二次元配列で緯度経度が入っている
lats, lons = grb_1.latlons()

#一次元に変換
# 二次元のままでは描画できない
# 2次元の格子点を1次元配列にならす
flat_lats= np.ravel(lats)
flat_lons= np.ravel(lons)

pd_rad= {'lons':flat_lons, 'lats':flat_lats}
pd_Uwind= {'lons':flat_lons, 'lats':flat_lats}
pd_Vwind= {'lons':flat_lons, 'lats':flat_lats}
pd_temp= {'lons':flat_lons, 'lats':flat_lats}

i,j,k,l =0,0,0,0

for grb in grbs:
    print(grb)
    
    if grb.name == "Downward short-wave radiation flux":
        radiation = grb.values
        flat_radiation = np.ravel(radiation)
        pd_name="radiation FH"+str(i)+"-"+str(i+1)+"W/m2(avg)"
        pd_rad[pd_name]=flat_radiation
        i=i+1

    elif grb.name == "10 metre U wind component":
        Uwind = grb.values
        flat_Uwind = np.ravel(Uwind)
        pd_name="Uwind FH"+str(j)+"m/s"
        pd_Uwind[pd_name]=flat_Uwind
        j=j+1

    elif grb.name == "10 metre V wind component":
        Vwind = grb.values
        flat_Vwind = np.ravel(Vwind)
        pd_name="Vwind FH"+str(k)+"m/s"
        pd_Uwind[pd_name]=flat_Uwind
        k=k+1

    elif grb.name == "Temperature":
        temperature = grb.values
        #華氏を摂氏に変換
        flat_temperature= np.ravel(temperature)
        flat_temperature=flat_temperature-273.115
        pd_name="temperature FH"+str(l)
        pd_temp[pd_name]=flat_temperature
        l=l+1

1:Pressure reduced to MSL:Pa (instant):regular_ll:meanSea:level 0:fcst time 0 hrs:from 201905220000
2:Surface pressure:Pa (instant):regular_ll:surface:level 0:fcst time 0 hrs:from 201905220000
3:10 metre U wind component:m s**-1 (instant):regular_ll:heightAboveGround:level 10 m:fcst time 0 hrs:from 201905220000
4:10 metre V wind component:m s**-1 (instant):regular_ll:heightAboveGround:level 10 m:fcst time 0 hrs:from 201905220000
5:Temperature:K (instant):regular_ll:heightAboveGround:level 1.5 m:fcst time 0 hrs:from 201905220000
6:Relative humidity:% (instant):regular_ll:heightAboveGround:level 1.5 m:fcst time 0 hrs:from 201905220000
7:Low cloud cover:% (instant):regular_ll:surface:level 0:fcst time 0 hrs:from 201905220000
8:Medium cloud cover:% (instant):regular_ll:surface:level 0:fcst time 0 hrs:from 201905220000
9:High cloud cover:% (instant):regular_ll:surface:level 0:fcst time 0 hrs:from 201905220000
10:Total cloud cover:% (instant):regular_ll:surface:level 0:fcst time 0 hrs:from 2

100:Relative humidity:% (instant):regular_ll:heightAboveGround:level 1.5 m:fcst time 8 hrs:from 201905220000
101:Low cloud cover:% (instant):regular_ll:surface:level 0:fcst time 8 hrs:from 201905220000
102:Medium cloud cover:% (instant):regular_ll:surface:level 0:fcst time 8 hrs:from 201905220000
103:High cloud cover:% (instant):regular_ll:surface:level 0:fcst time 8 hrs:from 201905220000
104:Total cloud cover:% (instant):regular_ll:surface:level 0:fcst time 8 hrs:from 201905220000
105:Total precipitation:kg m-2 (accum):regular_ll:surface:level 0:fcst time 7-8 hrs (accum):from 201905220000
106:Downward short-wave radiation flux:W m**-2 (avg):regular_ll:surface:level 0:fcst time 7-8 hrs (avg):from 201905220000
107:Pressure reduced to MSL:Pa (instant):regular_ll:meanSea:level 0:fcst time 9 hrs:from 201905220000
108:Surface pressure:Pa (instant):regular_ll:surface:level 0:fcst time 9 hrs:from 201905220000
109:10 metre U wind component:m s**-1 (instant):regular_ll:heightAboveGround:level 1

In [6]:
#緯度経度の範囲を選択
east_lon=131.69
west_lon=129.4337
north_lat=34.1413
south_lat=31.01

In [7]:
#range adjust
def range_ajust(east_lon,west_lon,north_lat,south_lat,df_all):
    df=df_all[df_all['lons'] > west_lon]
    df=df[df['lons'] < east_lon]

    df=df[df['lats'] > south_lat]
    df=df[df['lats'] < north_lat]
    return df



## Select parameter temperature, Uwind, Vwind, radiation

In [8]:
########################
df_para = "temperature"
########################

if df_para == "temperature":
    df_input=pd.DataFrame(pd_temp)

elif df_para == "Uwind":
    df_input=pd.DataFrame(pd_Uwind)
   
elif df_para == "Vwind":
    df_input=pd.DataFrame(pd_Vwind)
    
elif df_para == "radiation":
    df_input=pd.DataFrame(pd_rad)
    


df = range_ajust(east_lon,west_lon,north_lat,south_lat,df_input)
map_lat=df['lats'].values
map_lon=df['lons'].values
df = np.round(df,2)
print(len(df))
df[:10]

2294


lons  lats  temperature FH0  temperature FH1  temperature FH2  \
130021  129.44  34.1            19.76            19.90            19.78   
130022  129.50  34.1            19.77            19.96            19.85   
130023  129.56  34.1            19.77            19.98            19.92   
130024  129.62  34.1            19.74            19.95            19.97   
130025  129.69  34.1            19.73            19.91            20.00   
130026  129.75  34.1            19.70            19.86            20.02   
130027  129.81  34.1            19.69            19.80            20.00   
130028  129.88  34.1            19.67            19.76            19.96   
130029  129.94  34.1            19.67            19.72            19.92   
130030  130.00  34.1            19.69            19.69            19.87   

        temperature FH3  temperature FH4  temperature FH5  temperature FH6  \
130021            19.73            19.83            19.92            19.89   
130022            19.73            19.81            19.93            19.89   
130023            19.76            19.81            19.94            19.91   
130024            19.77            19.78            19.93            19.91   
130025            19.77            19.74            19.91            19.90   
130026            19.78            19.71            19.87            19.89   
130027            19.78            19.69            19.82            19.87   
130028            19.80            19.67            19.76            19.85   
130029            19.85            19.67            19.73            19.82   
130030            19.90            19.68            19.70            19.81   

        temperature FH7  temperature FH8  temperature FH9  temperature FH10  \
130021            19.96            20.07            20.13             20.20   
130022            19.98            20.10            20.18             20.25   
130023            20.00            20.12            20.21             20.27   
130024            19.99            20.12            20.20             20.26   
130025            19.96            20.10            20.18             20.23   
130026            19.93            20.07            20.15             20.19   
130027            19.88            20.02            20.10             20.14   
130028            19.85            19.97            20.04             20.07   
130029            19.82            19.91            19.99             20.02   
130030            19.80            19.87            19.95             20.00   

        temperature FH11  temperature FH12  temperature FH13  \
130021             20.16             20.14             20.10   
130022             20.19             20.17             20.12   
130023             20.20             20.19             20.13   
130024             20.19             20.16             20.12   
130025             20.16             20.12             20.08   
130026             20.12             20.08             20.03   
130027             20.06             20.01             19.95   
130028             19.99             19.92             19.85   
130029             19.92             19.83             19.74   
130030             19.88             19.75             19.63   

        temperature FH14  temperature FH15  
130021             20.03             19.98  
130022             20.04             20.01  
130023             20.06             20.01  
130024             20.03             20.00  
130025             19.98             19.95  
130026             19.93             19.89  
130027             19.86             19.82  
130028             19.78             19.75  
130029             19.67             19.64  
130030             19.57             19.54

In [9]:
FH0=df.iloc[:,2].values
FH1=df.iloc[:,3].values
FH2=df.iloc[:,4].values
FH3=df.iloc[:,5].values
FH4=df.iloc[:,6].values
FH5=df.iloc[:,7].values

In [10]:
from folium import plugins

#lat-long of focus area and zoom start
map = folium.Map([33.518022,130.471583], zoom_start=12)

# Mapbox makes some nice map tiles,
# Stamen also produce some cool map tiles which typically work at all zoom levels.
tile = folium.TileLayer('Stamen Terrain').add_to(map)

#adding marker and popup of temperature
for i in range(0,len(map_lat)):
    
    icon_number = plugins.BeautifyIcon(
    border_color='#00ABDC',
    text_color='#00ABDC',
    border_width=2,
    number=str(int(FH0[i])),
    inner_icon_style='margin-top:0;')
    
    folium.Marker(location=[float(map_lat[i])  ,float(map_lon[i])],\
                  popup="___"+df_para+"___"+"\n"\
                          +"__lat= "+str(map_lat[i])+"__\n"\
                          +"__lon= "+str(map_lon[i])+"__\n"\
                          +"__FH0= "+str(FH0[i])+"__\n"\
                          +"__FH1 = "+str(FH1[i])+"__\n"\
                          +"__FH2 = "+str(FH2[i])+"__\n"\
                          +"__FH3 = "+str(FH3[i])+"__\n"\
                          +"__FH4 = "+str(FH4[i])+"__\n"\
                          +"__FH5 = "+str(FH5[i])+"__\n",\
                 icon=icon_number).add_to(map)
    
#we can change tiles with help of LayerConrol
folium.LayerControl().add_to(map)

#Adding mouse position
formatter = "function(num) {return L.Util.formatNum(num, 3) + ' º ';};"

folium.plugins.MousePosition(
    position='topright',
    separator=' | ',
    empty_string='NaN',
    lng_first=True,
    num_digits=20,
    prefix='Coordinates:',
    lat_formatter=formatter,
    lng_formatter=formatter
).add_to(map)

map_name="Output_MAP/"+"FH_"+df_para+"_Map_" + year + "_" + month + "_" + day+ "_" + roottime+".html"
csv_name="Output_CSV/"+"FH_"+df_para + year + "_" + month + "_" + day+ "_" + roottime+".csv"

df.to_csv(csv_name, encoding='utf-8', index=False)
map.save(outfile=map_name)

map

In [11]:
elapsed_time = time.time() - start

print("elapsed_time:{0}".format(elapsed_time))

elapsed_time:17.28061819076538
